Story of what has worked and what didn't:<br>
1. since the data was anonymised, all the techniques I had used to comprehend what's actually in the columns of the data was to no avail. Also the fact that the almost every column was binary only added the fuel.
2. So, I introduced polynomial interactions between the three continuous features, which actually gave me better results.
3. Using custom class weights for each class helped hugely.
4. I had learned the presence of skew in the continuous features during my initial data understanding; and treatment of which didn't work and further more results were very very bad.
5. A LightGBM with some tuned parameters and some that I usually use pushed me up on the leaderboard.

In [ ]:
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
sns.set_style('darkgrid')

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [ ]:
from scipy import stats
from scipy.special import boxcox1p

from tqdm import tqdm_notebook

from sklearn.preprocessing import PolynomialFeatures

from sklearn.model_selection import StratifiedShuffleSplit

from lightgbm import LGBMClassifier

In [ ]:
train_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/Machine Hack/Challenges/Detecting Anomalies in Wafer Manufacturing/Participants_Data_WH18/Train.csv')
test_df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/Machine Hack/Challenges/Detecting Anomalies in Wafer Manufacturing/Participants_Data_WH18/Test.csv')
sample_submission = pd.read_csv('/content/drive/My Drive/Colab Notebooks/Machine Hack/Challenges/Detecting Anomalies in Wafer Manufacturing/Participants_Data_WH18/Sample_submission.csv')
train_df.shape, test_df.shape, sample_submission.shape

((1763, 1559), (756, 1558), (756, 1))

In [ ]:
pd.set_option('display.max_columns', 1600)
train_df

feature_1  feature_2  feature_3  feature_4  feature_5  feature_6  \
0           100        160     1.6000          0          0          0   
1            20         83     4.1500          1          0          0   
2            99        150     1.5151          1          0          0   
3            40         40     1.0000          0          0          0   
4            12        234    19.5000          1          0          0   
...         ...        ...        ...        ...        ...        ...   
1758          1          1     2.0000          1          0          0   
1759         40        200     5.0000          1          0          0   
1760         96        218     2.2708          1          0          0   
1761         16         81     5.0625          1          0          0   
1762         36         41     1.1388          0          0          0   

      feature_7  feature_8  feature_9  feature_10  feature_11  feature_12  \
0             0          0          0           0           0           0   
1             0          0          0           1           0           0   
2             0          0          0           0           0           0   
3             0          0          0           0           0           0   
4             0          0          0           0           0           0   
...         ...        ...        ...         ...         ...         ...   
1758          0          0          0           0           0           0   
1759          0          0          0           0           0           0   
1760          0          0          0           0           0           0   
1761          1          0          0           0           0           0   
1762          0          0          0           0           0           0   

      feature_13  feature_14  feature_15  feature_16  feature_17  feature_18  \
0              0           0           0           0           0           0   
1              0           0           0           0           0           0   
2              0           0           0           0           0           0   
3              0           0           0           0           0           0   
4              0           0           0           0           0           0   
...          ...         ...         ...         ...         ...         ...   
1758           0           0           0           0           0           0   
1759           0           0           0           0           0           0   
1760           0           0           0           0           0           0   
1761           0           0           0           0           0           0   
1762           0           0           0           0           0           0   

      feature_19  feature_20  feature_21  feature_22  feature_23  feature_24  \
0              0           0           0           0           0           0   
1              0           0           0           0           0           0   
2              0           0           0           0           0           0   
3              0           1           0           0           0           0   
4              0           0           0           0           0           0   
...          ...         ...         ...         ...         ...         ...   
1758           0           1           0           0           0           0   
1759           0           0           0           0           0           0   
1760           0           0           0           0           0           0   
1761           0           0           0           0           0           0   
1762           0           0           0           0           0           0   

      feature_25  feature_26  feature_27  feature_28  feature_29  feature_30  \
0              0           0           0           0           0           0   
1              0           0           0           0           0           0   
2              0           0  

1. check for columns that have only one value
2. check for columns that has same data as other columns

In [ ]:
train_df.describe()

feature_1    feature_2    feature_3    feature_4    feature_5  \
count  1763.000000  1763.000000  1763.000000  1763.000000  1763.000000   
mean     53.094158   126.587067     3.423940     0.724334     0.002836   
std      55.842014   129.859641     4.566858     0.446976     0.053194   
min       1.000000     1.000000     0.001500     0.000000     0.000000   
25%      12.000000    33.500000     1.250000     0.000000     0.000000   
50%      39.000000    96.000000     2.000000     1.000000     0.000000   
75%      75.000000   159.000000     4.500000     1.000000     0.000000   
max     640.000000   640.000000    60.000000     1.000000     1.000000   

         feature_6    feature_7    feature_8    feature_9   feature_10  \
count  1763.000000  1763.000000  1763.000000  1763.000000  1763.000000   
mean      0.002836     0.007941     0.002269     0.004538     0.012479   
std       0.053194     0.088783     0.047592     0.067229     0.111041   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max       1.000000     1.000000     1.000000     1.000000     1.000000   

        feature_11   feature_12   feature_13   feature_14   feature_15  \
count  1763.000000  1763.000000  1763.000000  1763.000000  1763.000000   
mean      0.002269     0.006239     0.006239     0.004538     0.006239   
std       0.047592     0.078765     0.078765     0.067229     0.078765   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max       1.000000     1.000000     1.000000     1.000000     1.000000   

        feature_16   feature_17   feature_18   feature_19   feature_20  \
count  1763.000000  1763.000000  1763.000000  1763.000000  1763.000000   
mean      0.004538     0.002836     0.003971     0.006239     0.004538   
std       0.067229     0.053194     0.062905     0.078765     0.067229   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max       1.000000     1.000000     1.000000     1.000000     1.000000   

        feature_21   feature_22   feature_23   feature_24   feature_25  \
count  1763.000000  1763.000000  1763.000000  1763.000000  1763.000000   
mean      0.002269     0.006239     0.005672     0.002836     0.003971   
std       0.047592     0.078765     0.075121     0.053194     0.062905   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max       1.000000     1.000000     1.000000     1.000000     1.000000   

        feature_26   feature_27   feature_28   feature_29   feature_30  \
count  1763.000000  1763.000000  1763.000000  1763.000000  1763.000000   
mean      0.003971     0.003971     0.003403     0.002269     0.005672   
std       0.062905     0.062905     0.058255     0.047592     0.075121   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       0.000000     0.000000     0.000000     0.000000     0.000000   
50%       0.000000     0.000000     0.000000     0.000000     0.000000   
75%       0.000000     0.000000     0.000000     0.000000     0.000000   
max       1.000000     1.000000     1.000000     1.000000     1.000000   

       

In [ ]:
train_binary_val_counts = train_df.iloc[:,3:].apply(pd.Series.value_counts).T
train_binary_val_counts

0       1
feature_4      486.0  1277.0
feature_5     1758.0     5.0
feature_6     1758.0     5.0
feature_7     1749.0    14.0
feature_8     1759.0     4.0
...              ...     ...
feature_1555  1736.0    27.0
feature_1556  1737.0    26.0
feature_1557  1746.0    17.0
feature_1558  1761.0     2.0
Class         1620.0   143.0

[1556 rows x 2 columns]

In [ ]:
pd.set_option('display.max_rows', 1600)
train_binary_val_counts.sort_values(by=1)

0       1
feature_309   1762.0     1.0
feature_1108  1762.0     1.0
feature_369   1762.0     1.0
feature_116   1762.0     1.0
feature_46    1762.0     1.0
feature_354   1762.0     1.0
feature_180   1762.0     1.0
feature_1320  1762.0     1.0
feature_1070  1762.0     1.0
feature_1245  1762.0     1.0
feature_78    1762.0     1.0
feature_83    1762.0     1.0
feature_1128  1762.0     1.0
feature_1034  1762.0     1.0
feature_150   1762.0     1.0
feature_1033  1762.0     1.0
feature_568   1762.0     1.0
feature_1269  1762.0     1.0
feature_1007  1762.0     1.0
feature_1013  1762.0     1.0
feature_803   1761.0     2.0
feature_812   1761.0     2.0
feature_821   1761.0     2.0
feature_827   1761.0     2.0
feature_845   1761.0     2.0
feature_1002  1761.0     2.0
feature_905   1761.0     2.0
feature_1006  1761.0     2.0
feature_932   1761.0     2.0
feature_792   1761.0     2.0
feature_947   1761.0     2.0
feature_326   1761.0     2.0
feature_317   1761.0     2.0
feature_863   1761.0     2.0
feature_786   1761.0     2.0
feature_1558  1761.0     2.0
feature_570   1761.0     2.0
feature_143   1761.0     2.0
feature_606   1761.0     2.0
feature_616   1761.0     2.0
feature_1427  1761.0     2.0
feature_622   1761.0     2.0
feature_629   1761.0     2.0
feature_161   1761.0     2.0
feature_463   1761.0     2.0
feature_448   1761.0     2.0
feature_663   1761.0     2.0
feature_791   1761.0     2.0
feature_127   1761.0     2.0
feature_438   1761.0     2.0
feature_1529  1761.0     2.0
feature_422   1761.0     2.0
feature_414   1761.0     2.0
feature_727   1761.0     2.0
feature_397   1761.0     2.0
feature_741   1761.0     2.0
feature_757   1761.0     2.0
feature_770   1761.0     2.0
feature_1361  1761.0     2.0
feature_177   1761.0     2.0
feature_688   1761.0     2.0
feature_210   1761.0     2.0
feature_77    1761.0     2.0
feature_307   1761.0     2.0
feature_1095  1761.0     2.0
feature_1099  1761.0     2.0
feature_1106  1761.0     2.0
feature_1116  1761.0     2.0
feature_281   1761.0     2.0
feature_261   1761.0     2.0
feature_49    1761.0     2.0
feature_1194  1761.0     2.0
feature_198   1761.0     2.0
feature_222   1761.0     2.0
feature_1309  1761.0     2.0
feature_1256  1761.0     2.0
feature_1278  1761.0     2.0
feature_1302  1761.0     2.0
feature_1203  1761.0     2.0
feature_292   1761.0     2.0
feature_1156  1761.0     2.0
feature_153   1761.0     2.0
feature_63    1761.0     2.0
feature_303   1761.0     2.0
feature_55    1761.0     2.0
feature_1171  1760.0     3.0
feature_1177  1760.0     3.0
feature_958   1760.0     3.0
feature_1197  1760.0     3.0
feature_446   1760.0     3.0
feature_1213  1760.0     3.0
feature_163   1760.0     3.0
feature_974   1760.0     3.0
feature_310   1760.0     3.0
feature_1042  1760.0     3.0
feature_62    1760.0     3.0
feature_1259  1760.0     3.0
feature_614   1760.0     3.0
feature_1306  1760.0     3.0
feature_1270  1760.0     3.0
feature_1287  1760.0     3.0
feature_1443  1760.0     3.0
feature_523   1760.0     3.0
feature_189   1760.0     3.0
feature_1163  1760.0     3.0
feature_1157  1760.0     3.0
feature_350   1760.0     3.0
feature_1134  1760.0     3.0
feature_1115  1760.0     3.0
feature_797   1760.0     3.0
feature_1126  1760.0     3.0
feature_392   1760.0     3.0
feature_1333  1760.0     3.0
feature_1332  1760.0     3.0
feature_1350  1760.0     3.0
feature_776   1760.0     3.0
feature_1072  1760.0     3.0
feature_1331  1760.0     3.0
feature_856   1760.0     3.0
feature_280   1760.0     3.0
feature_109   1760.0     3.0
feature_1092  1760.0     3.0
feature_1359  1760.0     3.0
feature_1089  1760.0     3.0
feature_1080  1760.0     3.0
feature_380   1760.0     3.0
feature_1408  1760.0     3.0
feature_1065  1760.0     3.0
feature_365   1759.0     4.0
feature_520   1759.0     4.0
feature_1486  1759.0     4.0
feature_509   1759.0     4.0
feature_503   1759.0     4.0
feature_396   1759.0     4.0
feature_218   1759.0     4.0
feature_470   1759.0     4.0
feature_231   1759.0     4.0
feature_445   175

In [ ]:
train_binary_val_counts.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1556 entries, feature_4 to Class
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   0       1556 non-null   float64
 1   1       1520 non-null   float64
dtypes: float64(2)
memory usage: 36.5+ KB


In [ ]:
columns_to_drop = train_binary_val_counts.loc[train_binary_val_counts.loc[:,1].isnull()].index.tolist()
columns_to_drop

['feature_57',
 'feature_82',
 'feature_106',
 'feature_147',
 'feature_262',
 'feature_278',
 'feature_284',
 'feature_320',
 'feature_362',
 'feature_372',
 'feature_383',
 'feature_435',
 'feature_439',
 'feature_488',
 'feature_495',
 'feature_522',
 'feature_531',
 'feature_553',
 'feature_578',
 'feature_591',
 'feature_630',
 'feature_631',
 'feature_652',
 'feature_894',
 'feature_934',
 'feature_978',
 'feature_1038',
 'feature_1063',
 'feature_1096',
 'feature_1185',
 'feature_1211',
 'feature_1243',
 'feature_1247',
 'feature_1341',
 'feature_1367',
 'feature_1407']

In [ ]:
# let's drop these columns, since they don't have any useful information to capture
train_df.drop(columns=columns_to_drop, axis=1, inplace=True)
train_df.shape

(1763, 1523)

In [ ]:
# duplicate column check

# create an empty dataframe with same index as above, which will be filled by factorized version on original data.
train_enc = pd.DataFrame(index=train_df.index)
# now encode all the features 
for col in tqdm_notebook(train_df.columns):
    train_enc[col] = train_df[col].factorize()[0]
# find and print duplicated columns
dup_cols = {}
# start with one feature
for i, c1 in enumerate(tqdm_notebook(train_enc.columns)):
    # compare it all the remaining features
    for c2 in train_enc.columns[i + 1:]:
        # add the entries to above dict, if matches with the column in first loop
        if c2 not in dup_cols and np.all(train_enc[c1] == train_enc[c2]):
            dup_cols[c2] = c1
# now print dup_cols dictionary would have names of columns as keys that are identical to a column in value.
print(dup_cols)

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:6: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:11: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  # This is added back by InteractiveShellApp.init_path()



{'feature_245': 'feature_6', 'feature_487': 'feature_6', 'feature_596': 'feature_6', 'feature_332': 'feature_7', 'feature_619': 'feature_7', 'feature_707': 'feature_7', 'feature_960': 'feature_7', 'feature_1286': 'feature_7', 'feature_353': 'feature_8', 'feature_365': 'feature_8', 'feature_696': 'feature_8', 'feature_953': 'feature_8', 'feature_962': 'feature_8', 'feature_1249': 'feature_8', 'feature_1321': 'feature_8', 'feature_16': 'feature_9', 'feature_125': 'feature_9', 'feature_417': 'feature_9', 'feature_469': 'feature_9', 'feature_525': 'feature_9', 'feature_396': 'feature_11', 'feature_423': 'feature_11', 'feature_445': 'feature_11', 'feature_520': 'feature_11', 'feature_699': 'feature_11', 'feature_780': 'feature_11', 'feature_1357': 'feature_11', 'feature_1385': 'feature_11', 'feature_1413': 'feature_11', 'feature_15': 'feature_12', 'feature_70': 'feature_12', 'feature_305': 'feature_12', 'feature_39': 'feature_14', 'feature_112': 'feature_14', 'feature_343': 'feature_17', '

In [ ]:
train_df.drop(columns=dup_cols.keys(), axis=1, inplace=True)
train_df.shape

(1763, 729)

In [ ]:
train_df

feature_1  feature_2  feature_3  feature_4  feature_5  feature_6  \
0           100        160     1.6000          0          0          0   
1            20         83     4.1500          1          0          0   
2            99        150     1.5151          1          0          0   
3            40         40     1.0000          0          0          0   
4            12        234    19.5000          1          0          0   
...         ...        ...        ...        ...        ...        ...   
1758          1          1     2.0000          1          0          0   
1759         40        200     5.0000          1          0          0   
1760         96        218     2.2708          1          0          0   
1761         16         81     5.0625          1          0          0   
1762         36         41     1.1388          0          0          0   

      feature_7  feature_8  feature_9  feature_10  feature_11  feature_12  \
0             0          0          0           0           0           0   
1             0          0          0           1           0           0   
2             0          0          0           0           0           0   
3             0          0          0           0           0           0   
4             0          0          0           0           0           0   
...         ...        ...        ...         ...         ...         ...   
1758          0          0          0           0           0           0   
1759          0          0          0           0           0           0   
1760          0          0          0           0           0           0   
1761          1          0          0           0           0           0   
1762          0          0          0           0           0           0   

      feature_13  feature_14  feature_17  feature_18  feature_19  feature_20  \
0              0           0           0           0           0           0   
1              0           0           0           0           0           0   
2              0           0           0           0           0           0   
3              0           0           0           0           0           1   
4              0           0           0           0           0           0   
...          ...         ...         ...         ...         ...         ...   
1758           0           0           0           0           0           1   
1759           0           0           0           0           0           0   
1760           0           0           0           0           0           0   
1761           0           0           0           0           0           0   
1762           0           0           0           0           0           0   

      feature_21  feature_22  feature_23  feature_24  feature_25  feature_26  \
0              0           0           0           0           0           0   
1              0           0           0           0           0           0   
2              0           0           0           0           0           0   
3              0           0           0           0           0           0   
4              0           0           0           0           0           0   
...          ...         ...         ...         ...         ...         ...   
1758           0           0           0           0           0           0   
1759           0           0           0           0           0           0   
1760           0           0           0           0           0           0   
1761           0           0           0           0           0           0   
1762           0           0           0           0           0           0   

      feature_27  feature_28  feature_29  feature_30  feature_31  feature_32  \
0              0           0           0           0           0           0   
1              0           0           0           0           0           0   
2              0           0  

In [ ]:
train_df.loc[:,'Class'].value_counts(normalize=True)

0    0.918888
1    0.081112
Name: Class, dtype: float64

In [ ]:
train_df.iloc[:,3:].apply(pd.Series.value_counts).T.sort_values(1, ascending=False)

0     1
feature_4      486  1277
feature_188   1253   510
feature_549   1411   352
feature_193   1429   334
feature_1137  1473   290
feature_1241  1486   277
feature_1279  1518   245
feature_574   1619   144
Class         1620   143
feature_65    1635   128
feature_1244  1639   124
feature_521   1646   117
feature_1437  1658   105
feature_352   1662   101
feature_1484  1665    98
feature_1436  1668    95
feature_1254  1669    94
feature_430   1671    92
feature_1400  1674    89
feature_1456  1674    89
feature_948   1677    86
feature_969   1682    81
feature_603   1685    78
feature_421   1688    75
feature_999   1692    71
feature_1352  1694    69
feature_885   1695    68
feature_1345  1697    66
feature_1154  1697    66
feature_266   1699    64
feature_1144  1699    64
feature_1383  1700    63
feature_552   1701    62
feature_555   1702    61
feature_1048  1705    58
feature_367   1705    58
feature_1044  1705    58
feature_1155  1706    57
feature_1368  1706    57
feature_1533  1707    56
feature_1395  1707    56
feature_1016  1707    56
feature_1109  1708    55
feature_1140  1708    55
feature_1027  1708    55
feature_458   1710    53
feature_1463  1711    52
feature_1075  1713    50
feature_963   1716    47
feature_236   1716    47
feature_1196  1718    45
feature_1019  1718    45
feature_1519  1720    43
feature_951   1721    42
feature_173   1722    41
feature_1230  1722    41
feature_1292  1723    40
feature_232   1723    40
feature_146   1724    39
feature_1090  1724    39
feature_1471  1725    38
feature_265   1725    38
feature_1523  1725    38
feature_1430  1725    38
feature_1264  1726    37
feature_347   1726    37
feature_656   1726    37
feature_1208  1726    37
feature_242   1727    36
feature_1538  1727    36
feature_1530  1727    36
feature_35    1728    35
feature_1514  1728    35
feature_121   1729    34
feature_810   1729    34
feature_235   1729    34
feature_442   1730    33
feature_1059  1730    33
feature_1503  1730    33
feature_1329  1730    33
feature_399   1730    33
feature_1222  1731    32
feature_1363  1732    31
feature_1470  1733    30
feature_1323  1734    29
feature_68    1734    29
feature_1480  1735    28
feature_646   1736    27
feature_1555  1736    27
feature_1474  1736    27
feature_701   1736    27
feature_341   1736    27
feature_1248  1736    27
feature_1141  1736    27
feature_1190  1736    27
feature_526   1736    27
feature_174   1737    26
feature_1527  1737    26
feature_1123  1737    26
feature_1501  1737    26
feature_501   1737    26
feature_1542  1737    26
feature_794   1737    26
feature_647   1738    25
feature_583   1738    25
feature_75    1738    25
feature_1296  1738    25
feature_378   1738    25
feature_1255  1738    25
feature_187   1738    25
feature_1061  1739    24
feature_1020  1739    24
feature_1001  1739    24
feature_1534  1739    24
feature_1023  1739    24
feature_318   1739    24
feature_546   1739    24
feature_766   1739    24
feature_1543  1740    23
feature_982   1740    23
feature_1505  1740    23
feature_48    1740    23
feature_1206  1740    23
feature_407   1741    22
feature_1528  1741    22
feature_539   1741    22
feature_277   1741    22
feature_10    1741    22
feature_609   1741    22
feature_1032  1741    22
feature_1212  1742    21
feature_1183  1742    21
feature_387   1742    21
feature_376   1742    21
feature_166   1742    21
feature_1482  1743    20
feature_1490  1743    20
feature_412   1743    20
feature_870   1743    20
feature_1468  1743    20
feature_530   1743    20
feature_1455  1743    20
feature_298   1743    20
feature_1489  1743    20
feature_1053  1743    20
feature_893   1743    20
feature_1097  1744    19
feature_875   1744    19
feature_1336  1744    19
feature_1469  1744    19
feature_983   1744    19
feature_1342  1744    19
feature_416   1744    19
feature_53    1744    19
feature_1504  1744    19
feature_283   1744    19
feature_1124  1744    19
feature_140   1744    19
feature_260   1745    18
feature_168   174

In [ ]:
pf = PolynomialFeatures(degree=3, interaction_only=False,  
                        include_bias=False)
pf_one = pf.fit_transform(train_df.loc[:, ['feature_1', 'feature_2', 'feature_3']])

pf_one.shape

(1763, 19)

In [ ]:
poly_features = pd.DataFrame(data=pf_one, columns=['pf_col_'+str(i) for i in range(1, 20)])
poly_features

pf_col_1  pf_col_2  pf_col_3  pf_col_4  pf_col_5  pf_col_6  pf_col_7  \
0        100.0     160.0    1.6000   10000.0   16000.0  160.0000   25600.0   
1         20.0      83.0    4.1500     400.0    1660.0   83.0000    6889.0   
2         99.0     150.0    1.5151    9801.0   14850.0  149.9949   22500.0   
3         40.0      40.0    1.0000    1600.0    1600.0   40.0000    1600.0   
4         12.0     234.0   19.5000     144.0    2808.0  234.0000   54756.0   
...        ...       ...       ...       ...       ...       ...       ...   
1758       1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
1759      40.0     200.0    5.0000    1600.0    8000.0  200.0000   40000.0   
1760      96.0     218.0    2.2708    9216.0   20928.0  217.9968   47524.0   
1761      16.0      81.0    5.0625     256.0    1296.0   81.0000    6561.0   
1762      36.0      41.0    1.1388    1296.0    1476.0   40.9968    1681.0   

       pf_col_8    pf_col_9  pf_col_10  pf_col_11   pf_col_12  pf_col_13  \
0      256.0000    2.560000  1000000.0  1600000.0  16000.0000  2560000.0   
1      344.4500   17.222500     8000.0    33200.0   1660.0000   137780.0   
2      227.2650    2.295528   970299.0  1470150.0  14849.4951  2227500.0   
3       40.0000    1.000000    64000.0    64000.0   1600.0000    64000.0   
4     4563.0000  380.250000     1728.0    33696.0   2808.0000   657072.0   
...         ...         ...        ...        ...         ...        ...   
1758     2.0000    4.000000        1.0        1.0      2.0000        1.0   
1759  1000.0000   25.000000    64000.0   320000.0   8000.0000  1600000.0   
1760   495.0344    5.156533   884736.0  2009088.0  20927.6928  4562304.0   
1761   410.0625   25.628906     4096.0    20736.0   1296.0000   104976.0   
1762    46.6908    1.296865    46656.0    53136.0   1475.8848    60516.0   

       pf_col_14    pf_col_15   pf_col_16     pf_col_17     pf_col_18  \
0     25600.0000   256.000000   4096000.0  4.096000e+04    409.600000   
1      6889.0000   344.450000    571787.0  2.858935e+04   1429.467500   
2     22499.2350   227.257273   3375000.0  3.408975e+04    344.329201   
3      1600.0000    40.000000     64000.0  1.600000e+03     40.000000   
4     54756.0000  4563.000000  12812904.0  1.067742e+06  88978.500000   
...          ...          ...         ...           ...           ...   
1758      2.0000     4.000000         1.0  2.000000e+00      4.000000   
1759  40000.0000  1000.000000   8000000.0  2.000000e+05   5000.000000   
1760  47523.3024   495.027133  10360232.0  1.079175e+05   1124.124116   
1761   6561.0000   410.062500    531441.0  3.321506e+04   2075.941406   
1762   1680.8688    46.687156     68921.0  1.914323e+03     53.171483   

        pf_col_19  
0        4.096000  
1       71.473375  
2        3.477954  
3        1.000000  
4     7414.875000  
...           ...  
1758     8.000000  
1759   125.000000  
1760    11.709454  
1761   129.746338  
1762     1.476870  

[1763 rows x 19 columns]

In [ ]:
train_df = pd.concat([train_df, poly_features], join='outer', axis=1)
train_df.head()

feature_1  feature_2  feature_3  feature_4  feature_5  feature_6  \
0        100        160     1.6000          0          0          0   
1         20         83     4.1500          1          0          0   
2         99        150     1.5151          1          0          0   
3         40         40     1.0000          0          0          0   
4         12        234    19.5000          1          0          0   

   feature_7  feature_8  feature_9  feature_10  feature_11  feature_12  \
0          0          0          0           0           0           0   
1          0          0          0           1           0           0   
2          0          0          0           0           0           0   
3          0          0          0           0           0           0   
4          0          0          0           0           0           0   

   feature_13  feature_14  feature_17  feature_18  feature_19  feature_20  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           1   
4           0           0           0           0           0           0   

   feature_21  feature_22  feature_23  feature_24  feature_25  feature_26  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_27  feature_28  feature_29  feature_30  feature_31  feature_32  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_33  feature_34  feature_35  feature_36  feature_37  feature_38  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_40  feature_41  feature_42  feature_43  feature_44  feature_45  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_46  feature_48  feature_49  feature_50  feature_51  feature_52  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           1           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_53  feature_54  feature_55  feature_56  feature_58  feature_59  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0        

In [ ]:
test_df.shape

(756, 1558)

In [ ]:
pf = PolynomialFeatures(degree=3, interaction_only=False,  
                        include_bias=False)
pf_one = pf.fit_transform(test_df .loc[:, ['feature_1', 'feature_2', 'feature_3']])

poly_features = pd.DataFrame(data=pf_one, columns=['pf_col_'+str(i) for i in range(1, 20)])
poly_features

pf_col_1  pf_col_2  pf_col_3  pf_col_4  pf_col_5  pf_col_6  pf_col_7  \
0        60.0     468.0    7.8000    3600.0   28080.0  468.0000  219024.0   
1       108.0     179.0    1.6574   11664.0   19332.0  178.9992   32041.0   
2         1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
3        60.0     468.0    7.8000    3600.0   28080.0  468.0000  219024.0   
4        60.0     120.0    2.0000    3600.0    7200.0  120.0000   14400.0   
5       125.0     125.0    1.0000   15625.0   15625.0  125.0000   15625.0   
6        60.0     468.0    7.8000    3600.0   28080.0  468.0000  219024.0   
7         1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
8        77.0      77.0    1.0000    5929.0    5929.0   77.0000    5929.0   
9       110.0     176.0    1.6000   12100.0   19360.0  176.0000   30976.0   
10       60.0     468.0    7.8000    3600.0   28080.0  468.0000  219024.0   
11       77.0     100.0    1.2987    5929.0    7700.0   99.9999   10000.0   
12        1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
13       32.0     259.0    8.0937    1024.0    8288.0  258.9984   67081.0   
14       36.0     140.0    3.8888    1296.0    5040.0  139.9968   19600.0   
15       15.0      15.0    1.0000     225.0     225.0   15.0000     225.0   
16       45.0     100.0    2.2222    2025.0    4500.0   99.9990   10000.0   
17       60.0     468.0    7.8000    3600.0   28080.0  468.0000  219024.0   
18       48.0     264.0    5.5000    2304.0   12672.0  264.0000   69696.0   
19       74.0      78.0    1.0540    5476.0    5772.0   77.9960    6084.0   
20      145.0     148.0    1.0206   21025.0   21460.0  147.9870   21904.0   
21       90.0      65.0    0.7222    8100.0    5850.0   64.9980    4225.0   
22       46.0      75.0    1.6304    2116.0    3450.0   74.9984    5625.0   
23       38.0      96.0    2.5263    1444.0    3648.0   95.9994    9216.0   
24       75.0      95.0    1.2666    5625.0    7125.0   94.9950    9025.0   
25       31.0      88.0    2.8387     961.0    2728.0   87.9997    7744.0   
26       62.0      82.0    1.3225    3844.0    5084.0   81.9950    6724.0   
27      117.0     115.0    0.9829   13689.0   13455.0  114.9993   13225.0   
28       50.0      82.0    1.6400    2500.0    4100.0   82.0000    6724.0   
29       60.0     468.0    7.8000    3600.0   28080.0  468.0000  219024.0   
30      108.0     229.0    2.1203   11664.0   24732.0  228.9924   52441.0   
31        1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
32       40.0      40.0    1.0000    1600.0    1600.0   40.0000    1600.0   
33       57.0      55.0    0.9649    3249.0    3135.0   54.9993    3025.0   
34       11.0      94.0    8.5454     121.0    1034.0   93.9994    8836.0   
35      161.0     119.0    0.7391   25921.0   19159.0  118.9951   14161.0   
36       27.0      69.0    2.5555     729.0    1863.0   68.9985    4761.0   
37      131.0     156.0    1.1908   17161.0   20436.0  155.9948   24336.0   
38      106.0     119.0    1.1226   11236.0   12614.0  118.9956   14161.0   
39      124.0     120.0    0.9677   15376.0   14880.0  119.9948   14400.0   
40       18.0      20.0    1.1111     324.0     360.0   19.9998     400.0   
41       36.0     180.0    5.0000    1296.0    6480.0  180.0000   32400.0   
42       32.0      88.0    2.7500    1024.0    2816.0   88.0000    7744.0   
43        1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
44       80.0      80.0    1.0000    6400.0    6400.0   80.0000    6400.0   
45        1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
46       49.0      49.0    1.0000    2401.0    2401.0   49.0000    2401.0   
47       90.0      60.0    0.6666    8100.0    5400.0   59.9940    3600.0   
48      149.0     182.0    1.2214   22201.0   27118.0  181.9886   33124.0   
49       31.0      88.0    2.8387     961.0    2728.0   87.9997    7744.0   
50        1.0       1.0    2.0000       1.0       1.0    2.0000       1.0   
5

In [ ]:
test_df = pd.concat([test_df, poly_features], join='outer', axis=1)
test_df.head()

feature_1  feature_2  feature_3  feature_4  feature_5  feature_6  \
0       60.0      468.0     7.8000        1.0          0          0   
1      108.0      179.0     1.6574        1.0          0          0   
2        1.0        1.0     2.0000        0.0          0          0   
3       60.0      468.0     7.8000        1.0          0          0   
4       60.0      120.0     2.0000        1.0          0          0   

   feature_7  feature_8  feature_9  feature_10  feature_11  feature_12  \
0          0          0          0           0           0           0   
1          0          0          0           0           0           0   
2          0          0          0           0           0           0   
3          0          0          0           0           0           0   
4          0          0          0           0           0           0   

   feature_13  feature_14  feature_15  feature_16  feature_17  feature_18  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_19  feature_20  feature_21  feature_22  feature_23  feature_24  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_25  feature_26  feature_27  feature_28  feature_29  feature_30  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_31  feature_32  feature_33  feature_34  feature_35  feature_36  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_37  feature_38  feature_39  feature_40  feature_41  feature_42  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_43  feature_44  feature_45  feature_46  feature_47  feature_48  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0           0           0           0   
4           0           0           0           0           0           0   

   feature_49  feature_50  feature_51  feature_52  feature_53  feature_54  \
0           0           0           0           0           0           0   
1           0           0           0           0           0           0   
2           0           0           0           0           0           0   
3           0           0           0        

# building a baseline

In [ ]:
from sklearn.model_selection import StratifiedShuffleSplit
strat_split = StratifiedShuffleSplit(n_splits=5, test_size=0.15, random_state=2)

for tr_index, val_index in strat_split.split(train_df, train_df.loc[:,'Class']):
    strat_train_df = train_df.loc[tr_index]
    strat_valid_df = train_df.loc[val_index]

strat_train_df.shape, strat_valid_df.shape

((1498, 748), (265, 748))

In [ ]:
strat_train_df.loc[:,'Class'].value_counts(normalize=True), strat_valid_df.loc[:,'Class'].value_counts(normalize=True)

(0    0.918558
 1    0.081442
 Name: Class, dtype: float64, 0    0.920755
 1    0.079245
 Name: Class, dtype: float64)

In [ ]:
strat_train_df.shape

(1498, 748)

In [ ]:
# making class weigts
new_maps = strat_train_df.loc[:,'Class'].value_counts()
new_maps = new_maps.to_dict()
Class_weights = {i:(1/new_maps[i])*(1_498)/2.0 for i in range(2)}
Class_weights

{0: 0.5443313953488372, 1: 6.139344262295082}

In [ ]:
lgbm_base_4 = None
lgbm_base_4 = LGBMClassifier(max_depth=9, num_leaves=100, learning_rate=0.01, n_estimators=10_000, colsample_bytree=0.85, objective='binary', subsample=1.0,
                             min_child_weight=7, class_weight=Class_weights, random_state=100)

lgbm_base_4.fit(X=strat_train_df.loc[:,strat_train_df.columns != 'Class'],
              y=strat_train_df.loc[:,'Class'],
              eval_set=[(strat_valid_df.loc[:,strat_valid_df.columns != 'Class'], strat_valid_df.loc[:,'Class'])],
              verbose=100, early_stopping_rounds=1_000, eval_metric='auc')

Training until validation scores don't improve for 1000 rounds.
[100]	valid_0's auc: 0.904469	valid_0's binary_logloss: 0.419158
[200]	valid_0's auc: 0.899493	valid_0's binary_logloss: 0.364928
[300]	valid_0's auc: 0.913251	valid_0's binary_logloss: 0.33785
[400]	valid_0's auc: 0.914227	valid_0's binary_logloss: 0.323803
[500]	valid_0's auc: 0.91774	valid_0's binary_logloss: 0.319687
[600]	valid_0's auc: 0.916179	valid_0's binary_logloss: 0.318675
[700]	valid_0's auc: 0.915593	valid_0's binary_logloss: 0.318707
[800]	valid_0's auc: 0.913447	valid_0's binary_logloss: 0.317546
[900]	valid_0's auc: 0.913251	valid_0's binary_logloss: 0.315868
[1000]	valid_0's auc: 0.914032	valid_0's binary_logloss: 0.31555
[1100]	valid_0's auc: 0.912861	valid_0's binary_logloss: 0.315005
[1200]	valid_0's auc: 0.912471	valid_0's binary_logloss: 0.314746
[1300]	valid_0's auc: 0.912471	valid_0's binary_logloss: 0.315189
[1400]	valid_0's auc: 0.911885	valid_0's binary_logloss: 0.314885
Early stopping, best ite

LGBMClassifier(boosting_type='gbdt',
               class_weight={0: 0.5443313953488372, 1: 6.139344262295082},
               colsample_bytree=0.85, importance_type='split',
               learning_rate=0.01, max_depth=9, min_child_samples=20,
               min_child_weight=7, min_split_gain=0.0, n_estimators=10000,
               n_jobs=-1, num_leaves=100, objective='binary', random_state=100,
               reg_alpha=0.0, reg_lambda=0.0, silent=True, subsample=1.0,
               subsample_for_bin=200000, subsample_freq=0)

In [ ]:
lgbm_base_preds = lgbm_base_4.predict(X=test_df)
lgbm_base_preds = pd.Series(lgbm_base_preds)
lgbm_base_preds = lgbm_base_preds.rename('Class')
lgbm_base_preds.to_csv(path_or_buf='/content/drive/My Drive/Colab Notebooks/Machine Hack/Challenges/Detecting Anomalies in Wafer Manufacturing/lgbm_base_4_preds.csv',
                       index=False)